In [3]:
from __future__ import division 
%matplotlib inline
#system
import time
import os
import gc
#third lib
import numpy as np
import pandas as pd
import lightgbm as lgb
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.cross_validation import train_test_split

In [4]:

gc.collect()
train_data = pd.read_csv('E:\\ATEC_FRAUD\\b_data\\atec_anti_fraud_train.csv')
test_data = pd.read_csv('E:\\ATEC_FRAUD\\b_data\\atec_anti_fraud_test_b.csv')
train_data.loc[train_data['label']==-1,'label'] =1
train_y = train_data['label']
train_data.drop(['id','label'],axis=1,inplace=True)

#train_data = train_data[list(fea_need[:feature_num]['col'])+['date']]
sub=pd.DataFrame()
sub['id'] =  test_data['id']
test_data.drop(['id'],axis=1,inplace=True)
#test_data = test_data[list(fea_need[:feature_num]['col'])+['date']]
train_size = len(train_data)
all_data = train_data.append(test_data)
all_data.shape

(1495269, 298)

In [5]:
train_data.shape

(994731, 298)

In [6]:
def get_train_test3(train_data, train_y, test_size=0.29293):
    
    import random
    
    
    X_train, X_val,y_train, y_val =train_test_split(train_data,train_y,test_size=0.30)
            
    return X_train, X_val, y_train, y_val
    
    
    

In [7]:
all_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1495269 entries, 0 to 500537
Columns: 298 entries, date to f297
dtypes: float64(279), int64(19)
memory usage: 3.3 GB


In [8]:
#这种处理的最终结果---0.27 非常不好
# train_data.drop(['date'],inplace=True,axis=1)
# test_data.drop(['date'],inplace=True,axis=1)
#now the feature 
def preprocess_likeo(df):
    num =0
    col_need =[ 'f1',
 'f2',
 'f3',
 'f4',
 'f5',
 'f6',
 'f7',
 'f8',
 'f9',
 'f10',
 'f11',
 'f12',
 'f13',
 'f14',
 'f15',
 'f16',
 'f17',
 'f18',
 'f19',
 'f212',
 'f213',
 'f214',
 'f215',
 'f216',
 'f217',
 'f218',
 'f219',
 'f220',
 'f221',
 'f222',
 'f224',
 'f225',
 'f226',
 'f227',
 'f228',
 'f229',
 'f231',
 'f232',
 'f233',
 'f235',
 'f236', 
 'f241',
 'f245',
 'f246',
 'f251',
 
'row_nan']
    
    for col in df.columns:
        
        #col_ratio = (len(df[col])-df[col].count())/len(df[col])
            
#         if(col not in col_need and col in col_need2):
#             df[col+'_nan'] = 0
#             df[col+'_nan'][df[col].isna()] = 1 
        if(col not in col_need):    
            df.drop([col],axis=1,inplace=True)
            num= num +1
            print('current and drop',num,col)
#         elif(col in ['f82','f83','f84','f85','f86']):
#             df[col].fillna(df[col].mean(),inplace=True)
      #  elif(col!='date' and (col  not in col_del) and int(df[col].unique().size) ==  int(df[col].max()-df[col].min() + 1)):
    #         df[col].fillna(df[col].mode(),inplace=True)
#         elif(col!='date'):
#             df[col].fillna(df[col].median(),inplace=True)
     #   else:
    #       df[col].fillna(df[col].median(),inplace=True)
    return df
            

#处理时间数据,将时间date这一列，处理成四列，分别是样本中的第几天、这年的第几天、这个月的第几天、这周的第几天
def time_feature(df):
    df['datetime']  = pd.to_datetime(df['date'],format="%Y%m%d")
    tmp = pd.DatetimeIndex(df['datetime'])
    das=df['datetime']
    daop = pd.DataFrame(dict(zip(*[["{}_{}".format(das.name, i) for i in ["Day","DayofYear", "DayofMonth", "DayofWeek"]], 
                                   [(das - das.min()).astype('timedelta64[D]').astype(int), tmp.dayofyear, tmp.day, tmp.dayofweek]])),
                        index = das.index)
    df=pd.concat([df,daop], axis = 1)
    df.drop("datetime",axis=1,inplace=True)
    return df

In [9]:
def data_rownan_cal(df):
    df['row_nan']=(1.000 - df.count(axis=1) /df.shape[1])
    return df

def preprocess_likeo(df):
    for col in df.columns:
        col_ratio = (len(df[col])-df[col].count())/len(df[col])
        if(col_ratio>0.90):
            df.drop([col],axis=1,inplace=True)
        elif(col_ratio>0.22):
            col_name = '{}_isna'.format(col)
            df[col_name]=df[col].apply(lambda x: 1 if np.isnan(x) else 0)
            df.drop([col],axis=1,inplace=True)
        else:
            df[col].fillna(df[col].median(),inplace=True)
    return df
            

#处理时间数据,将时间date这一列，处理成四列，分别是样本中的第几天、这年的第几天、这个月的第几天、这周的第几天
def time_feature(df):
    df['datetime']  = pd.to_datetime(df['date'],format="%Y%m%d")
    tmp = pd.DatetimeIndex(df['datetime'])
    das=df['datetime']
    daop = pd.DataFrame(dict(zip(*[["{}_{}".format(das.name, i) for i in ["Day","DayofYear", "DayofMonth", "DayofWeek"]], 
                                   [(das - das.min()).astype('timedelta64[D]').astype(int), tmp.dayofyear, tmp.day, tmp.dayofweek]])),
                        index = das.index)
    df=pd.concat([df,daop], axis = 1)
    df.drop("datetime",axis=1,inplace=True)
    return df

In [10]:
all_data = data_rownan_cal(all_data) 
all_data = preprocess_likeo(all_data)
#all_data = time_feature(all_data)

# train_data =  = preprocess_likeo(train_data)
# train_data = time_feature(train_data)



#all_data.drop(['date'],inplace=True,axis=1)


('current and drop', 1, 'date')
('current and drop', 2, 'f20')
('current and drop', 3, 'f21')
('current and drop', 4, 'f22')
('current and drop', 5, 'f23')
('current and drop', 6, 'f24')
('current and drop', 7, 'f25')
('current and drop', 8, 'f26')
('current and drop', 9, 'f27')
('current and drop', 10, 'f28')
('current and drop', 11, 'f29')
('current and drop', 12, 'f30')
('current and drop', 13, 'f31')
('current and drop', 14, 'f32')
('current and drop', 15, 'f33')
('current and drop', 16, 'f34')
('current and drop', 17, 'f35')
('current and drop', 18, 'f36')
('current and drop', 19, 'f37')
('current and drop', 20, 'f38')
('current and drop', 21, 'f39')
('current and drop', 22, 'f40')
('current and drop', 23, 'f41')
('current and drop', 24, 'f42')
('current and drop', 25, 'f43')
('current and drop', 26, 'f44')
('current and drop', 27, 'f45')
('current and drop', 28, 'f46')
('current and drop', 29, 'f47')
('current and drop', 30, 'f48')
('current and drop', 31, 'f49')
('current and dr

('current and drop', 248, 'f292')
('current and drop', 249, 'f293')
('current and drop', 250, 'f294')
('current and drop', 251, 'f295')
('current and drop', 252, 'f296')
('current and drop', 253, 'f297')


In [11]:
# train_data = preprocess_likeo(train_data)
# train_data = time_feature(train_data)

In [12]:
train_data = all_data[:train_size]
test_data = all_data[train_size:]
train_data.head()

f1  f2  f3  f4        f5  f6  f7  f8  f9  f10    ...     f231  f232  f233  \
0   0   0   0   0  100807.0   0   5   1   1    1    ...      3.0   3.0   4.0   
1   0   1   1   1  100805.0   1   5   2   1    1    ...      2.0   2.0   1.0   
2   0   0   1   0  100102.0   0   6   1   0    0    ...      1.0   1.0   2.0   
3   0   0   0   1  100807.0   1   4   1   2    2    ...      2.0   1.0   1.0   
4   1   1   0   1  100805.0   1   5   1   2    0    ...      2.0   2.0   2.0   

   f235  f236  f241  f245  f246  f251   row_nan  
0   2.0   2.0   3.0   5.0   5.0   4.0  0.040268  
1   2.0   1.0   2.0   2.0   1.0   2.0  0.040268  
2   1.0   2.0   2.0   2.0   2.0   2.0  0.540268  
3   1.0   2.0   2.0   1.0   1.0   1.0  0.365772  
4   3.0   2.0   1.0   2.0   2.0   2.0  0.040268  

[5 rows x 46 columns]

In [13]:
test_data.head()

f1  f2  f3  f4        f5  f6  f7  f8  f9  f10    ...     f231  f232  f233  \
0   0   0   1   1  100810.0   0   4   2   0    1    ...      1.0   3.0   4.0   
1   0   0   1   1  100810.0   1   6   1   0    2    ...      1.0   1.0   1.0   
2   0   0   1   1  100811.0   1   2   1   0    1    ...      2.0   2.0   2.0   
3   1   0   1   0  100811.0   0   5   1   2    1    ...      1.0   2.0   2.0   
4   0   0   1   1  100811.0   1   7   1   1    2    ...      1.0   1.0   2.0   

   f235  f236  f241  f245  f246  f251   row_nan  
0   2.0   8.0   2.0   3.0   7.0   3.0  0.365772  
1   1.0   1.0   2.0   2.0   1.0   2.0  0.100671  
2   2.0   1.0   1.0   1.0   1.0   1.0  0.365772  
3   2.0   2.0   2.0   3.0   3.0   1.0  0.365772  
4   9.0   9.0   1.0  10.0   9.0   1.0  0.426174  

[5 rows x 46 columns]

In [14]:
#test_data.drop(['date'],inplace=True,axis=1)

In [15]:
def feval_spec(preds, train_data):
    from sklearn.metrics import roc_curve
    fpr, tpr, threshold = roc_curve(train_data.get_label(), preds)
    tpr0001 = tpr[fpr <= 0.001].max()
    tpr001 = tpr[fpr <= 0.005].max()
    tpr005 = tpr[fpr <= 0.01].max()
    #tpr01 = tpr[fpr.values <= 0.01].max()
    tprcal = 0.4 * tpr0001 + 0.3 * tpr001 + 0.3 * tpr005
    return 'spec_cal',tprcal,True
lgb_params = {
    
     'boosting_type': 'gbdt', 
     'objective': 'binary', 
      'nthread': -1, 
    #'learning_rate': 0.01,
     # 'silent': True,
     'metric': 'auc',
#       'seed':77,
      'num_leaves': 200, 
      'learning_rate': 0.05, 
#       'max_depth': -1, 
#       'gamma':47,
#       'max_bin': 255, 
#       'subsample_for_bin': 70000, 
#       'bagging_fraction':0.7, 
#       'bagging_freq':1, 
#       'bagging_seed':55,
       'colsample_bytree': 0.6, 
#       'reg_alpha': 19.43, 
#       'reg_lambda': 0, 
#       'min_split_gain': 0.3512, 
#       'min_child_weight': 1,
#       'min_child_samples':1321, 
#       'scale_pos_weight':90,
#     'boosting_type': 'gbdt',
#     'objective': 'binary', #xentlambda
#    'learning_rate': 0.01,

#     # 'is_unbalance': 'true',  #because training data is unbalance (replaced with scale_pos_weight)
#     'num_leaves': 25,  # we should let it be smaller than 2^(max_depth)
#     'max_depth': -1,  # -1 means no limit
#     'metric' : 'feval_spec',
      #'min_child_samples': 100,  # Minimum number of data need in a child(min_data_in_leaf)
#     'min_data_in_leaf': 250,
#     'max_bin': 200,  # Number of bucketed bin for feature values
#      'subsample': 0.8,  # Subsample ratio of the training instance.
#     #'subsample_freq': 1,  # frequence of subsample, <=0 means no enable
#    'bagging_fraction': 0.8,
#    'bagging_freq': 10,
#     'colsample_bytree': 0.8,  # Subsample ratio of columns when constructing each tree.
#    # 'min_child_weight': 2,  # Minimum sum of instance weight(hessian) needed in a child(leaf)
#     'feature_fraction':0.8,  #new para control the feature be used.
#     'scale_pos_weight':90,
#     'subsample_for_bin': 200000,  # Number of samples for constructing bin
#     'min_split_gain': 5,  # lambda_l1, lambda_l2 and min_gain_to_split to regularization
#     'reg_alpha': 0.1,  # L1 regularization term on weights
#    'reg_lambda': 0.001,  # L2 regularization term on weights
#     'nthread': 10,
#     'verbose': 0
    
#         'learning_rate': 0.2,
#         #'is_unbalance': 'true', # replaced with scale_pos_weight argument
#         'num_leaves': 7,  # 2^max_depth - 1
         'max_depth': -1,  # -1 means no limit
#         'min_child_samples': 100,  # Minimum number of data need in a child(min_data_in_leaf)
#         'max_bin': 100,  # Number of bucketed bin for feature values
#        'subsample': 0.8,  # Subsample ratio of the training instance.
#         'subsample_freq': 1,  # frequence of subsample, <=0 means no enable
#         'colsample_bytree': 0.9,  # Subsample ratio of columns when constructing each tree.
#         'min_child_weight': 0,  # Minimum sum of instance weight(hessian) needed in a child(leaf)
#         'scale_pos_weight':200, # because training data is extremely unbalanced 
       
}


In [16]:
def po_predict(train_data, train_y,test_data, num,stacknum):
    #from sklearn.model_selection import StratifiedKFold
    #s5kf = StratifiedKFold(n_splits=cvnum,shuffle=True).split(train_data,train_y)
    result=[]
    model = []
    for i in range(num):
        #X_train, X_val, y_train, y_val = train_test_split(train_data, train_y, test_size=0.2)
        X_train, X_val, y_train, y_val  =get_train_test3(train_data, train_y, test_size=0.30)
        #X_train.drop(['date'],axis=1,inplace= True)
        #X_val.drop(['date'],axis=1,inplace= True)
        xgtrain = lgb.Dataset(X_train,y_train )
        xgvalid = lgb.Dataset(X_val, y_val)
        evals_results={}        
        bst1 = lgb.train(lgb_params,xgtrain,valid_sets=[xgtrain,xgvalid],valid_names=['train','valid'],evals_result=evals_results,
                num_boost_round=200,early_stopping_rounds=50, verbose_eval=True,feval=feval_spec)
            
        result.append(bst1.best_score)
        model.append(bst1)
        print('Best ite and score ',bst1.best_iteration,bst1.best_score)
        del X_train, X_val, y_train, y_val,xgtrain, xgvalid
        gc.collect()
    
    d_box_df=pd.DataFrame(columns=['test_valid'])
    for i in range(len(result)):
       d_box_df.loc[i,'test_valid'] = result[i]['valid']['spec_cal']
    d_box_df['model'] = list(model) 
    
    sorted_df = d_box_df.sort_values(by=['test_valid'],ascending=False)
    print(sorted_df)
    a_score=pd.DataFrame()
    for  j in range(stacknum):
        c_m_rname = 'm_{}'.format(j)
        c_m = sorted_df.loc[j,'model']
        a_score[c_m_rname] = c_m.predict(test_data,num_iteration=c_m.best_iteration)
    a_score_mean =  a_score.mean(axis=1)
    return sorted_df,a_score_mean

In [17]:
a_scr,sub['score'] = po_predict(train_data,train_y,test_data,10,5)
a_scr

[1]	train's auc: 0.898685	train's spec_cal: 0.285433	valid's auc: 0.89418	valid's spec_cal: 0.244701
Training until validation scores don't improve for 50 rounds.
[2]	train's auc: 0.915942	train's spec_cal: 0.305832	valid's auc: 0.910012	valid's spec_cal: 0.254292
[3]	train's auc: 0.91827	train's spec_cal: 0.33225	valid's auc: 0.912617	valid's spec_cal: 0.273081
[4]	train's auc: 0.919769	train's spec_cal: 0.339839	valid's auc: 0.913808	valid's spec_cal: 0.279376
[5]	train's auc: 0.920417	train's spec_cal: 0.342946	valid's auc: 0.914465	valid's spec_cal: 0.281172
[6]	train's auc: 0.921189	train's spec_cal: 0.342207	valid's auc: 0.914984	valid's spec_cal: 0.278863
[7]	train's auc: 0.921917	train's spec_cal: 0.344593	valid's auc: 0.916015	valid's spec_cal: 0.279218
[8]	train's auc: 0.927497	train's spec_cal: 0.34326	valid's auc: 0.922342	valid's spec_cal: 0.278054
[9]	train's auc: 0.930911	train's spec_cal: 0.346893	valid's auc: 0.925702	valid's spec_cal: 0.280442
[10]	train's auc: 0.9337

[81]	train's auc: 0.955546	train's spec_cal: 0.425161	valid's auc: 0.943893	valid's spec_cal: 0.322439
[82]	train's auc: 0.955923	train's spec_cal: 0.426154	valid's auc: 0.944205	valid's spec_cal: 0.32238
[83]	train's auc: 0.95609	train's spec_cal: 0.426681	valid's auc: 0.944216	valid's spec_cal: 0.322755
[84]	train's auc: 0.956327	train's spec_cal: 0.427699	valid's auc: 0.944351	valid's spec_cal: 0.322262
[85]	train's auc: 0.956599	train's spec_cal: 0.428234	valid's auc: 0.94441	valid's spec_cal: 0.322735
[86]	train's auc: 0.957063	train's spec_cal: 0.429287	valid's auc: 0.944716	valid's spec_cal: 0.322873
[87]	train's auc: 0.957331	train's spec_cal: 0.42961	valid's auc: 0.944873	valid's spec_cal: 0.322439
[88]	train's auc: 0.957523	train's spec_cal: 0.430467	valid's auc: 0.945009	valid's spec_cal: 0.322873
[89]	train's auc: 0.957717	train's spec_cal: 0.431104	valid's auc: 0.944911	valid's spec_cal: 0.324137
[90]	train's auc: 0.958165	train's spec_cal: 0.432148	valid's auc: 0.945238	v

[161]	train's auc: 0.980717	train's spec_cal: 0.487708	valid's auc: 0.95024	valid's spec_cal: 0.329347
[162]	train's auc: 0.98097	train's spec_cal: 0.488362	valid's auc: 0.950236	valid's spec_cal: 0.32982
[163]	train's auc: 0.981124	train's spec_cal: 0.489406	valid's auc: 0.950297	valid's spec_cal: 0.330215
[164]	train's auc: 0.98179	train's spec_cal: 0.489686	valid's auc: 0.950287	valid's spec_cal: 0.329939
[165]	train's auc: 0.981948	train's spec_cal: 0.490654	valid's auc: 0.95036	valid's spec_cal: 0.329899
[166]	train's auc: 0.982129	train's spec_cal: 0.491469	valid's auc: 0.95039	valid's spec_cal: 0.329978
[167]	train's auc: 0.982326	train's spec_cal: 0.492105	valid's auc: 0.950425	valid's spec_cal: 0.329998
[168]	train's auc: 0.982626	train's spec_cal: 0.493209	valid's auc: 0.950397	valid's spec_cal: 0.330649
[169]	train's auc: 0.983197	train's spec_cal: 0.493854	valid's auc: 0.950368	valid's spec_cal: 0.330353
[170]	train's auc: 0.983375	train's spec_cal: 0.495407	valid's auc: 0.

[37]	train's auc: 0.940128	train's spec_cal: 0.391319	valid's auc: 0.931527	valid's spec_cal: 0.315906
[38]	train's auc: 0.940609	train's spec_cal: 0.392365	valid's auc: 0.931804	valid's spec_cal: 0.314786
[39]	train's auc: 0.940985	train's spec_cal: 0.392314	valid's auc: 0.932028	valid's spec_cal: 0.315199
[40]	train's auc: 0.941345	train's spec_cal: 0.393028	valid's auc: 0.932311	valid's spec_cal: 0.315651
[41]	train's auc: 0.941723	train's spec_cal: 0.393887	valid's auc: 0.932541	valid's spec_cal: 0.315926
[42]	train's auc: 0.942002	train's spec_cal: 0.395358	valid's auc: 0.932989	valid's spec_cal: 0.316398
[43]	train's auc: 0.942129	train's spec_cal: 0.395417	valid's auc: 0.932939	valid's spec_cal: 0.316241
[44]	train's auc: 0.942592	train's spec_cal: 0.395842	valid's auc: 0.933302	valid's spec_cal: 0.316457
[45]	train's auc: 0.942885	train's spec_cal: 0.396063	valid's auc: 0.933659	valid's spec_cal: 0.317342
[46]	train's auc: 0.943092	train's spec_cal: 0.396888	valid's auc: 0.9338

[117]	train's auc: 0.967523	train's spec_cal: 0.455276	valid's auc: 0.947007	valid's spec_cal: 0.329021
[118]	train's auc: 0.967993	train's spec_cal: 0.455956	valid's auc: 0.947127	valid's spec_cal: 0.329552
[119]	train's auc: 0.968161	train's spec_cal: 0.45639	valid's auc: 0.947247	valid's spec_cal: 0.32908
[120]	train's auc: 0.968454	train's spec_cal: 0.457827	valid's auc: 0.947202	valid's spec_cal: 0.329139
[121]	train's auc: 0.968727	train's spec_cal: 0.458167	valid's auc: 0.947338	valid's spec_cal: 0.328903
[122]	train's auc: 0.969006	train's spec_cal: 0.459085	valid's auc: 0.94745	valid's spec_cal: 0.329512
[123]	train's auc: 0.969265	train's spec_cal: 0.459833	valid's auc: 0.947718	valid's spec_cal: 0.33024
[124]	train's auc: 0.969737	train's spec_cal: 0.460862	valid's auc: 0.947813	valid's spec_cal: 0.330476
[125]	train's auc: 0.970092	train's spec_cal: 0.461925	valid's auc: 0.947874	valid's spec_cal: 0.330849
[126]	train's auc: 0.970484	train's spec_cal: 0.463005	valid's auc: 

...

[167]	train's auc: 0.9825	train's spec_cal: 0.492889	valid's auc: 0.953118	valid's spec_cal: 0.339968
[168]	train's auc: 0.98273	train's spec_cal: 0.493301	valid's auc: 0.953101	valid's spec_cal: 0.339847
[169]	train's auc: 0.983233	train's spec_cal: 0.493949	valid's auc: 0.953112	valid's spec_cal: 0.339887
[170]	train's auc: 0.983324	train's spec_cal: 0.494976	valid's auc: 0.953124	valid's spec_cal: 0.339948
[171]	train's auc: 0.983585	train's spec_cal: 0.495531	valid's auc: 0.953106	valid's spec_cal: 0.339726
[172]	train's auc: 0.98372	train's spec_cal: 0.497088	valid's auc: 0.953199	valid's spec_cal: 0.340068
[173]	train's auc: 0.983902	train's spec_cal: 0.498022	valid's auc: 0.953235	valid's spec_cal: 0.340411
[174]	train's auc: 0.984053	train's spec_cal: 0.498704	valid's auc: 0.953318	valid's spec_cal: 0.340371
[175]	train's auc: 0.984223	train's spec_cal: 0.49968	valid's auc: 0.953328	valid's spec_cal: 0.340552
[176]	train's auc: 0.98446	train's spec_cal: 0.500328	valid's auc: 0.

[43]	train's auc: 0.942375	train's spec_cal: 0.398626	valid's auc: 0.934226	valid's spec_cal: 0.318768
[44]	train's auc: 0.94287	train's spec_cal: 0.398728	valid's auc: 0.934575	valid's spec_cal: 0.318612
[45]	train's auc: 0.943511	train's spec_cal: 0.399283	valid's auc: 0.934967	valid's spec_cal: 0.320366
[46]	train's auc: 0.943806	train's spec_cal: 0.399539	valid's auc: 0.935226	valid's spec_cal: 0.320659
[47]	train's auc: 0.944051	train's spec_cal: 0.400794	valid's auc: 0.935956	valid's spec_cal: 0.320074
[48]	train's auc: 0.944166	train's spec_cal: 0.400956	valid's auc: 0.936094	valid's spec_cal: 0.320288
[49]	train's auc: 0.94445	train's spec_cal: 0.40192	valid's auc: 0.936383	valid's spec_cal: 0.320074
[50]	train's auc: 0.94484	train's spec_cal: 0.402714	valid's auc: 0.936656	valid's spec_cal: 0.319782
[51]	train's auc: 0.945198	train's spec_cal: 0.404165	valid's auc: 0.936705	valid's spec_cal: 0.320113
[52]	train's auc: 0.945939	train's spec_cal: 0.404831	valid's auc: 0.93708	va

[123]	train's auc: 0.968995	train's spec_cal: 0.462735	valid's auc: 0.948384	valid's spec_cal: 0.333502
[124]	train's auc: 0.969656	train's spec_cal: 0.463392	valid's auc: 0.948528	valid's spec_cal: 0.333502
[125]	train's auc: 0.969993	train's spec_cal: 0.464459	valid's auc: 0.948613	valid's spec_cal: 0.333171
[126]	train's auc: 0.9703	train's spec_cal: 0.465978	valid's auc: 0.948707	valid's spec_cal: 0.334028
[127]	train's auc: 0.970486	train's spec_cal: 0.467079	valid's auc: 0.94879	valid's spec_cal: 0.334223
[128]	train's auc: 0.970753	train's spec_cal: 0.468231	valid's auc: 0.948878	valid's spec_cal: 0.334106
[129]	train's auc: 0.971068	train's spec_cal: 0.468974	valid's auc: 0.948928	valid's spec_cal: 0.334477
[130]	train's auc: 0.971387	train's spec_cal: 0.469222	valid's auc: 0.948974	valid's spec_cal: 0.334594
[131]	train's auc: 0.971545	train's spec_cal: 0.469606	valid's auc: 0.949041	valid's spec_cal: 0.335295
[132]	train's auc: 0.971718	train's spec_cal: 0.471441	valid's auc:

  test_valid                                              model
4   0.351262  <lightgbm.basic.Booster object at 0x0000000018...
3   0.350227  <lightgbm.basic.Booster object at 0x0000000006...
7   0.343942  <lightgbm.basic.Booster object at 0x0000000018...
2   0.342834  <lightgbm.basic.Booster object at 0x0000000004...
6   0.342827  <lightgbm.basic.Booster object at 0x0000000018...
8    0.34168  <lightgbm.basic.Booster object at 0x0000000004...
5   0.340872  <lightgbm.basic.Booster object at 0x0000000018...
9   0.337498  <lightgbm.basic.Booster object at 0x000000000B...
1   0.335627  <lightgbm.basic.Booster object at 0x0000000006...
0   0.330097  <lightgbm.basic.Booster object at 0x0000000017...


test_valid                                              model
4   0.351262  <lightgbm.basic.Booster object at 0x0000000018...
3   0.350227  <lightgbm.basic.Booster object at 0x0000000006...
7   0.343942  <lightgbm.basic.Booster object at 0x0000000018...
2   0.342834  <lightgbm.basic.Booster object at 0x0000000004...
6   0.342827  <lightgbm.basic.Booster object at 0x0000000018...
8    0.34168  <lightgbm.basic.Booster object at 0x0000000004...
5   0.340872  <lightgbm.basic.Booster object at 0x0000000018...
9   0.337498  <lightgbm.basic.Booster object at 0x000000000B...
1   0.335627  <lightgbm.basic.Booster object at 0x0000000006...
0   0.330097  <lightgbm.basic.Booster object at 0x0000000017...

In [18]:
a_scr

test_valid                                              model
4   0.351262  <lightgbm.basic.Booster object at 0x0000000018...
3   0.350227  <lightgbm.basic.Booster object at 0x0000000006...
7   0.343942  <lightgbm.basic.Booster object at 0x0000000018...
2   0.342834  <lightgbm.basic.Booster object at 0x0000000004...
6   0.342827  <lightgbm.basic.Booster object at 0x0000000018...
8    0.34168  <lightgbm.basic.Booster object at 0x0000000004...
5   0.340872  <lightgbm.basic.Booster object at 0x0000000018...
9   0.337498  <lightgbm.basic.Booster object at 0x000000000B...
1   0.335627  <lightgbm.basic.Booster object at 0x0000000006...
0   0.330097  <lightgbm.basic.Booster object at 0x0000000017...

In [19]:
#a_scr.to_csv('E:\\ATEC_FRAUD\\boxplot\\'+'200_withfillbase_{}.csv'.format(int(time.time())), index= False)

In [20]:
sub.head(10)

id     score
0  661ae9a03c6c74feab2555c9987e140ae3f5421bd8e7a0...  0.003799
1  ada98d4358e72a27cc5e92f691a87a4fd62a7cda0387e2...  0.000676
2  e33675a962e5bf44d05a2b01903a4beb88a0c6385c05c6...  0.001426
3  4c5da176de7172dbd1ad0aa7edf9866548ec720d6c7318...  0.011243
4  fa39e3491900d49b862d30b5dbcd0b1c30bb4ff0d96396...  0.018579
5  ae0f1ecb27e098bbf672529a50237dff27abd16b349569...  0.000283
6  7a9e5e415412a92928f91608c39750e3a33eb123eb0ef8...  0.013312
7  51fb55256e959c36989151e8136a8a68002bb75887eb75...  0.018761
8  aa7664463d11ae5573ae6d89195373fbe033c354710142...  0.003514
9  b794af5790f98806ff8ad8ee268caa606dffcfbcb753bd...  0.013979

In [21]:
a_scr.loc[0,'model'].predict(test_data,num_iteration=a_scr.loc[0,'model'].best_iteration)[:10]

array([0.00335914, 0.00041889, 0.00145775, 0.00951369, 0.01955253,
       0.00028569, 0.01407155, 0.00256786, 0.00233152, 0.01272169])

In [22]:
a_scr.loc[0,'model'].predict(test_data,num_iteration=1)[:10]

array([0.47514407, 0.47514407, 0.47514407, 0.47576099, 0.47567699,
       0.47514407, 0.47530181, 0.47514407, 0.47548018, 0.47834836])

In [23]:
import time
path_save='E:\\ATEC_FRAUD\\e_predicB\\'
sub.to_csv(path_save+'submissiomean20810706_{}.csv'.format(int(time.time())), index=False,float_format='%.9f')


In [24]:
import os
os.environ["PATH"] += os.pathsep + 'c:/Program Files (x86)/Graphviz2.38/bin/'
ax = lgb.plot_tree(a_scr.loc[0,'model'], tree_index=a_scr.loc[0,'model'].best_iteration-1, figsize=(400, 380), show_info=['split_gain','internal_value', 'internal_count', 'leaf_count'])
plt.show()

In [25]:
mm=pd.DataFrame()
mm['col'] = list(train_data.columns)
mm['fea']=a_scr.loc[0,'model'].feature_importance()
mm.sort_values(by=['fea'],ascending=False)

col   fea
4        f5  2932
22     f215  2009
25     f218  1940
6        f7  1560
42     f245  1509
43     f246  1508
40     f236  1474
39     f235  1387
24     f217  1208
23     f216  1197
45  row_nan  1140
14      f15   962
17      f18   958
13      f14   953
16      f17   908
5        f6   884
21     f214   798
18      f19   796
38     f233   789
29     f222   713
32     f226   700
44     f251   700
8        f9   697
35     f229   696
11      f12   689
41     f241   671
10      f11   654
37     f232   625
9       f10   619
15      f16   581
3        f4   567
36     f231   563
12      f13   560
31     f225   522
0        f1   493
33     f227   484
7        f8   482
26     f219   477
27     f220   476
19     f212   452
20     f213   447
34     f228   442
2        f3   422
30     f224   418
28     f221   411
1        f2   327

In [26]:
list(mm.sort_values(by=['fea'],ascending=False)['col'])

['f5',
 'f215',
 'f218',
 'f7',
 'f245',
 'f246',
 'f236',
 'f235',
 'f217',
 'f216',
 'row_nan',
 'f15',
 'f18',
 'f14',
 'f17',
 'f6',
 'f214',
 'f19',
 'f233',
 'f222',
 'f226',
 'f251',
 'f9',
 'f229',
 'f12',
 'f241',
 'f11',
 'f232',
 'f10',
 'f16',
 'f4',
 'f231',
 'f13',
 'f225',
 'f1',
 'f227',
 'f8',
 'f219',
 'f220',
 'f212',
 'f213',
 'f228',
 'f3',
 'f224',
 'f221',
 'f2']